In [4]:
!pip install --upgrade google-adk google-genai google-colab PyPDF2 pillow

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 5.6 MB/s eta 0:00:00


In [13]:
from google.colab import userdata, files
import os
import asyncio
from google.adk.agents import LlmAgent
from google.adk.runners import Runner
from google.adk.sessions import InMemorySessionService
from google.genai import types
import PyPDF2
import base64

# 3️⃣ Set Gemini API Key
try:
    os.environ['GEMINI_API_KEY'] = userdata.get('GOOGLE_API_KEY')
    # CHANGED MODEL HERE: Reverting to gemini-2.5-flash for multimodal support
    LLM_MODEL = "gemini-2.5-flash"
    print("✅ API Key set successfully; using model =", LLM_MODEL)
except Exception:
    print("❌ ERROR: Please set 'GOOGLE_API_KEY' in Colab Secrets before running.")
    raise

# 4️⃣ Create StudyBuddy agent
studybuddy_agent = LlmAgent(
    name="StudyBuddy",
    model=LLM_MODEL,
    instruction=(
        "You are StudyBuddy, a friendly AI tutor. "
        "You can answer questions, explain concepts, and analyze text, images, and PDFs. "
        "Always give helpful examples and include at least one emoji. "
        "When analyzing an image, provide a detailed description and context."
    ),
    description="An AI tutor that helps students learn with text, images, and PDFs."
)

# 5️⃣ Setup session
APP_NAME = "studybuddy_app"
USER_ID = "colab_user"
SESSION_ID = "studybuddy_session"

session_service = InMemorySessionService()
await session_service.create_session(
    app_name=APP_NAME,
    user_id=USER_ID,
    session_id=SESSION_ID
)

# 6️⃣ Create Runner
runner = Runner(
    agent=studybuddy_agent,
    app_name=APP_NAME,
    session_service=session_service
)

# 7️⃣ Function to process queries
async def run_query(query_text=None, pdf_path=None, image_data=None):
    parts = []

    if query_text:
        parts.append(types.Part(text=query_text))

    if image_data:
        parts.append(types.Part(
            inline_data=types.Blob(
                mime_type="image/jpeg", # Defaulting to JPEG, but ADK is flexible with actual type
                data=image_data
            )
        ))

    if pdf_path:
        pdf_text = ""
        with open(pdf_path, "rb") as f:
            reader = PyPDF2.PdfReader(f)
            for page in reader.pages:
                pdf_text += page.extract_text() + "\n"
        parts.append(types.Part(text=pdf_text))

    content = types.Content(role="user", parts=parts)
    final_response_text = "Agent did not produce a final response."

    async for event in runner.run_async(
        user_id=USER_ID,
        session_id=SESSION_ID,
        new_message=content
    ):
        if event.is_final_response() and event.content and event.content.parts:
            final_response_text = "".join(p.text for p in event.content.parts if p.text)
            break

    return final_response_text

# 8️⃣ Interactive loop with safe multimodal support
async def interactive_studybuddy():
    print("👋 Welcome to StudyBuddy! You can ask questions, upload images or PDFs. Type 'exit' to quit.\n")

    while True:
        print("Options:")
        print("1. Text question")
        print("2. Upload an image")
        print("3. Upload a PDF")
        user_choice = input("Select option (1/2/3) or type 'exit': ").strip()

        if user_choice.lower() in ["exit", "quit"]:
            print("👋 Goodbye! Happy studying!")
            break

        if user_choice == "1":
            query_text = input("💬 Your Question: ").strip()
            response = await run_query(query_text=query_text)

        elif user_choice == "2":
            uploaded = files.upload()
            if not uploaded:
                print("❌ No image uploaded. Please try again.\n")
                continue

            image_filename = next(iter(uploaded))
            image_data = uploaded[image_filename]

            print(f"✅ Image '{image_filename}' uploaded. Now, what's your question about it?")
            follow_up_question = input("💬 Your question about the image: ").strip()

            query_with_filename = f"Regarding the image '{image_filename}', {follow_up_question}"
            response = await run_query(query_text=query_with_filename, image_data=image_data)

        elif user_choice == "3":
            uploaded = files.upload()
            if not uploaded:
                print("❌ No PDF uploaded. Please try again.\n")
                continue
            pdf_path = next(iter(uploaded))
            response = await run_query(pdf_path=pdf_path)

        else:
            print("❌ Invalid option. Try again.\n")
            continue

        print(f"🤖 StudyBuddy: {response}\n")

# 9️⃣ Run the interactive agent
await interactive_studybuddy()

✅ API Key set successfully; using model = gemini-2.5-flash
👋 Welcome to StudyBuddy! You can ask questions, upload images or PDFs. Type 'exit' to quit.

Options:
1. Text question
2. Upload an image
3. Upload a PDF
Select option (1/2/3) or type 'exit': 2


Saving Gemini_Generated_Image_xcon7jxcon7jxcon.png to Gemini_Generated_Image_xcon7jxcon7jxcon (6).png
✅ Image 'Gemini_Generated_Image_xcon7jxcon7jxcon (6).png' uploaded. Now, what's your question about it?
💬 Your question about the image: What can you see in the image
🤖 StudyBuddy: This image beautifully captures a dedicated study environment, likely belonging to someone engaged in learning about technology and artificial intelligence. 🧠

Here's a detailed description of what I can see:

*   **Study Desk Setup:** The primary focus is a wooden desk filled with various study materials. The lighting suggests a warm, possibly late afternoon or early morning glow coming from a window on the left.
*   **Open Book on AI:** In the center, there's a thick, open textbook titled "Introduction to Artificial Intelligence." Several lines of text on the pages are highlighted in yellow, indicating active reading and note-taking.
*   **Laptop:** To the left, a silver laptop is open, displaying what app

Saving test.pdf to test.pdf
🤖 StudyBuddy: Thanks for sharing the "StudyBuddy Agent Testing Document"! It's a concise and clear overview of some fundamental concepts in Artificial Intelligence. This document seems perfectly designed to introduce these key areas. 👍

Here's an analysis of the concepts presented:

The document introduces four core areas within Artificial Intelligence:

1.  **Machine Learning (ML):** This is presented as a foundational subset of AI. The key idea here is that ML algorithms learn from data *without explicit programming*. Over time, through experience with data, they improve their performance on specific tasks.
    *   **Example:** A spam filter that learns to identify new types of spam emails based on patterns in past emails it has encountered.

2.  **Deep Learning (DL):** This is a more specialized subfield *within* Machine Learning. It stands out because it utilizes "deep" neural networks – networks with many layers – to uncover intricate patterns in data. 